In [49]:
# !pip install scipy
# !pip install pysindy plotly

In [77]:
import numpy as np
import plotly.graph_objs as go
from scipy.integrate import solve_ivp
import pysindy as ps

# Параметры системы Лоренца
sigma = 10.0
rho = 28.0
beta = 8.0 / 3.0

# Уравнения Лоренца
def lorenz(t, state):
    x, y, z = state
    dxdt = sigma * (y - x)
    dydt = x * (rho - z) - y
    dzdt = x * y - beta * z
    return [dxdt, dydt, dzdt]

# Начальные условия и время интегрирования
initial_state = [1.0, 1.0, 1.0]
t_span = (0, 149)  # временной интервал
t_eval = np.linspace(t_span[0], t_span[1], 30000)  # временные точки

# Интеграция системы
sol = solve_ivp(lorenz, t_span, initial_state, t_eval=t_eval)
x = sol.y[0]

# Создание векторов задержки
tau = 13
embedding_dim = 3

def delay_embedding(data, delay, dim):
    n = len(data)
    max_delay = (dim - 1) * delay
    embedded_data = np.zeros((n - max_delay, dim))
    for i in range(dim):
        embedded_data[:, i] = data[delay * i:n - max_delay + delay * i]
    return embedded_data

embedded_data = delay_embedding(x, tau, embedding_dim)

# Create an interactive Plotly graph
fig = go.Figure(data=[go.Scatter3d(
    x=embedded_data[:, 0],
    y=embedded_data[:, 1],
    z=embedded_data[:, 2],
    mode='lines',
    line=dict(color='blue', width=2)
)])

# Configure the layout of the graph
fig.update_layout(
    title="Reconstructed Lorenz Attractor using Delay Embedding",
    scene=dict(
        xaxis_title='x(t)',
        yaxis_title=f'x(t-{tau})',
        zaxis_title=f'x(t-{2*tau})'
    ),
    width=800,
    height=600,
    margin=dict(l=0, r=0, b=0, t=40)
)

# Display the graph
fig.show()


In [78]:
# Задержка времени (шаг)
dt = t_eval[1] - t_eval[0]
from sklearn.linear_model import Lasso
from pysindy.optimizers import SR3
# Обучение модели SINDy
model = ps.SINDy(optimizer=SR3(threshold=0.1, nu=1.0))
# model = ps.SINDy(optimizer=ps.STLSQ(threshold=0.0133))
model.fit(embedded_data, t=dt)
model.print()

(x0)' = -20.335 x0 + 27.828 x1 + -7.387 x2 + 0.001 x0 x1
(x1)' = -8.406 x0 + 8.406 x2
(x2)' = 7.388 x0 + -27.830 x1 + 20.337 x2


In [79]:
# Прогнозирование и визуализация
simulated_data = model.simulate(embedded_data[0], t_eval)
# sol = solve_ivp(sindy_eqs, t_span, initial_state, t_eval=t_eval)
# simulated_data = sol.y

In [80]:
# Построение интерактивного графика с Plotly
fig = go.Figure()

# Восстановленные данные
fig.add_trace(go.Scatter3d(
    x=embedded_data[:, 0], y=embedded_data[:, 1], z=embedded_data[:, 2],
    mode='lines', name='Reconstructed',
    line=dict(color='blue', width=2)
))

# Симулированные данные
fig.add_trace(go.Scatter3d(
    x=simulated_data[:, 0], y=simulated_data[:, 1], z=simulated_data[:, 2],
    mode='lines', name='Simulated',
    line=dict(color='red', width=2)
))

# Настройки графика
fig.update_layout(
    title='Reconstructed Lorenz Attractor and SINDy Simulation',
    scene=dict(
        xaxis_title='x(t)',
        yaxis_title=f'x(t-{tau})',
        zaxis_title=f'x(t-{2*tau})'
    ),
    width=800,
    height=600
)

fig.show()